In [1]:
import gym
import numpy as np

#MAX_NUM_EPISODES = 500
MAX_NUM_EPISODES = 50000
STEPS_PER_EPISODE = 200 #  This is specific to MountainCar. May change with env
EPSILON_MIN = 0.005
max_num_steps = MAX_NUM_EPISODES * STEPS_PER_EPISODE
EPSILON_DECAY = 500 * EPSILON_MIN / max_num_steps
ALPHA = 0.05  # Learning rate
GAMMA = 0.98  # Discount factor
NUM_DISCRETE_BINS = 30  # Number of bins to Discretize each observation dim


class Q_Learner(object):
    def __init__(self, env):
        self.obs_shape = env.observation_space.shape
        self.obs_high = env.observation_space.high
        self.obs_low = env.observation_space.low
        self.obs_bins = NUM_DISCRETE_BINS  # Number of bins to Discretize each observation dim
        self.bin_width = (self.obs_high - self.obs_low) / self.obs_bins
        self.action_shape = env.action_space.n
        # Create a multi-dimensional array (aka. Table) to represent the
        # Q-values
        self.Q = np.zeros((self.obs_bins + 1, self.obs_bins + 1,
                           self.action_shape))  # (51 x 51 x 3)
        self.alpha = ALPHA  # Learning rate
        self.gamma = GAMMA  # Discount factor
        self.epsilon = 1.0

    def discretize(self, obs):
        return tuple(((obs - self.obs_low) / self.bin_width).astype(int))

    def get_action(self, obs):
        discretized_obs = self.discretize(obs)
        # Epsilon-Greedy action selection
        if self.epsilon > EPSILON_MIN:
            self.epsilon -= EPSILON_DECAY
        if np.random.random() > self.epsilon:
            return np.argmax(self.Q[discretized_obs])
        else:  # Choose a random action
            return np.random.choice([a for a in range(self.action_shape)])

    def learn(self, obs, action, reward, next_obs):
        discretized_obs = self.discretize(obs)
        discretized_next_obs = self.discretize(next_obs)
        td_target = reward + self.gamma * np.max(self.Q[discretized_next_obs])
        td_error = td_target - self.Q[discretized_obs][action]
        self.Q[discretized_obs][action] += self.alpha * td_error

def train(agent, env):
    best_reward = -float('inf')
    for episode in range(MAX_NUM_EPISODES):
        done = False
        obs = env.reset()
        total_reward = 0.0
        while not done:
            action = agent.get_action(obs)
            next_obs, reward, done, info = env.step(action)
            agent.learn(obs, action, reward, next_obs)
            obs = next_obs
            total_reward += reward
        if total_reward > best_reward:
            best_reward = total_reward
        print("Episode#:{} reward:{} best_reward:{} eps:{}".format(episode,
                                     total_reward, best_reward, agent.epsilon))
    # Return the trained policy
    return np.argmax(agent.Q, axis=2)


def test(agent, env, policy):
    done = False
    obs = env.reset()
    total_reward = 0.0
    while not done:
        action = policy[agent.discretize(obs)]
        next_obs, reward, done, info = env.step(action)
        obs = next_obs
        total_reward += reward
    return total_reward


if __name__ == "__main__":
    env = gym.make('MountainCar-v0')
    agent = Q_Learner(env)
    learned_policy = train(agent, env)
    # Use the Gym Monitor wrapper to evalaute the agent and record video
    gym_monitor_path = "./gym_monitor_output"
    env = gym.wrappers.Monitor(env, gym_monitor_path, force=True)
    for _ in range(1000):
        test(agent, env, learned_policy)
    env.close()



Episode#:0 reward:-200.0 best_reward:-200.0 eps:0.999949999999993
Episode#:1 reward:-200.0 best_reward:-200.0 eps:0.999899999999986
Episode#:2 reward:-200.0 best_reward:-200.0 eps:0.999849999999979
Episode#:3 reward:-200.0 best_reward:-200.0 eps:0.999799999999972
Episode#:4 reward:-200.0 best_reward:-200.0 eps:0.999749999999965
Episode#:5 reward:-200.0 best_reward:-200.0 eps:0.9996999999999581
Episode#:6 reward:-200.0 best_reward:-200.0 eps:0.9996499999999511
Episode#:7 reward:-200.0 best_reward:-200.0 eps:0.9995999999999441
Episode#:8 reward:-200.0 best_reward:-200.0 eps:0.9995499999999371
Episode#:9 reward:-200.0 best_reward:-200.0 eps:0.9994999999999301
Episode#:10 reward:-200.0 best_reward:-200.0 eps:0.9994499999999231
Episode#:11 reward:-200.0 best_reward:-200.0 eps:0.9993999999999161
Episode#:12 reward:-200.0 best_reward:-200.0 eps:0.9993499999999091
Episode#:13 reward:-200.0 best_reward:-200.0 eps:0.9992999999999022
Episode#:14 reward:-200.0 best_reward:-200.0 eps:0.999249999999

Episode#:124 reward:-200.0 best_reward:-200.0 eps:0.9937499999991264
Episode#:125 reward:-200.0 best_reward:-200.0 eps:0.9936999999991194
Episode#:126 reward:-200.0 best_reward:-200.0 eps:0.9936499999991124
Episode#:127 reward:-200.0 best_reward:-200.0 eps:0.9935999999991054
Episode#:128 reward:-200.0 best_reward:-200.0 eps:0.9935499999990984
Episode#:129 reward:-200.0 best_reward:-200.0 eps:0.9934999999990914
Episode#:130 reward:-200.0 best_reward:-200.0 eps:0.9934499999990845
Episode#:131 reward:-200.0 best_reward:-200.0 eps:0.9933999999990775
Episode#:132 reward:-200.0 best_reward:-200.0 eps:0.9933499999990705
Episode#:133 reward:-200.0 best_reward:-200.0 eps:0.9932999999990635
Episode#:134 reward:-200.0 best_reward:-200.0 eps:0.9932499999990565
Episode#:135 reward:-200.0 best_reward:-200.0 eps:0.9931999999990495
Episode#:136 reward:-200.0 best_reward:-200.0 eps:0.9931499999990425
Episode#:137 reward:-200.0 best_reward:-200.0 eps:0.9930999999990355
Episode#:138 reward:-200.0 best_re

Episode#:249 reward:-200.0 best_reward:-200.0 eps:0.9874999999982528
Episode#:250 reward:-200.0 best_reward:-200.0 eps:0.9874499999982458
Episode#:251 reward:-200.0 best_reward:-200.0 eps:0.9873999999982388
Episode#:252 reward:-200.0 best_reward:-200.0 eps:0.9873499999982318
Episode#:253 reward:-200.0 best_reward:-200.0 eps:0.9872999999982248
Episode#:254 reward:-200.0 best_reward:-200.0 eps:0.9872499999982178
Episode#:255 reward:-200.0 best_reward:-200.0 eps:0.9871999999982108
Episode#:256 reward:-200.0 best_reward:-200.0 eps:0.9871499999982039
Episode#:257 reward:-200.0 best_reward:-200.0 eps:0.9870999999981969
Episode#:258 reward:-200.0 best_reward:-200.0 eps:0.9870499999981899
Episode#:259 reward:-200.0 best_reward:-200.0 eps:0.9869999999981829
Episode#:260 reward:-200.0 best_reward:-200.0 eps:0.9869499999981759
Episode#:261 reward:-200.0 best_reward:-200.0 eps:0.9868999999981689
Episode#:262 reward:-200.0 best_reward:-200.0 eps:0.9868499999981619
Episode#:263 reward:-200.0 best_re

Episode#:373 reward:-200.0 best_reward:-200.0 eps:0.9812999999973862
Episode#:374 reward:-200.0 best_reward:-200.0 eps:0.9812499999973792
Episode#:375 reward:-200.0 best_reward:-200.0 eps:0.9811999999973722
Episode#:376 reward:-200.0 best_reward:-200.0 eps:0.9811499999973652
Episode#:377 reward:-200.0 best_reward:-200.0 eps:0.9810999999973582
Episode#:378 reward:-200.0 best_reward:-200.0 eps:0.9810499999973512
Episode#:379 reward:-200.0 best_reward:-200.0 eps:0.9809999999973442
Episode#:380 reward:-200.0 best_reward:-200.0 eps:0.9809499999973372
Episode#:381 reward:-200.0 best_reward:-200.0 eps:0.9808999999973302
Episode#:382 reward:-200.0 best_reward:-200.0 eps:0.9808499999973233
Episode#:383 reward:-200.0 best_reward:-200.0 eps:0.9807999999973163
Episode#:384 reward:-200.0 best_reward:-200.0 eps:0.9807499999973093
Episode#:385 reward:-200.0 best_reward:-200.0 eps:0.9806999999973023
Episode#:386 reward:-200.0 best_reward:-200.0 eps:0.9806499999972953
Episode#:387 reward:-200.0 best_re

Episode#:493 reward:-200.0 best_reward:-200.0 eps:0.9752999999965475
Episode#:494 reward:-200.0 best_reward:-200.0 eps:0.9752499999965405
Episode#:495 reward:-200.0 best_reward:-200.0 eps:0.9751999999965335
Episode#:496 reward:-200.0 best_reward:-200.0 eps:0.9751499999965265
Episode#:497 reward:-200.0 best_reward:-200.0 eps:0.9750999999965195
Episode#:498 reward:-200.0 best_reward:-200.0 eps:0.9750499999965125
Episode#:499 reward:-200.0 best_reward:-200.0 eps:0.9749999999965056
Episode#:500 reward:-200.0 best_reward:-200.0 eps:0.9749499999964986
Episode#:501 reward:-200.0 best_reward:-200.0 eps:0.9748999999964916
Episode#:502 reward:-200.0 best_reward:-200.0 eps:0.9748499999964846
Episode#:503 reward:-200.0 best_reward:-200.0 eps:0.9747999999964776
Episode#:504 reward:-200.0 best_reward:-200.0 eps:0.9747499999964706
Episode#:505 reward:-200.0 best_reward:-200.0 eps:0.9746999999964636
Episode#:506 reward:-200.0 best_reward:-200.0 eps:0.9746499999964566
Episode#:507 reward:-200.0 best_re

...

Episode#:49439 reward:-121.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49440 reward:-145.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49441 reward:-124.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49442 reward:-122.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49443 reward:-124.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49444 reward:-200.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49445 reward:-125.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49446 reward:-118.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49447 reward:-120.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49448 reward:-154.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49449 reward:-155.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49450 reward:-182.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49451 reward:-123.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49452 reward:-117.0 best_reward:-89.0 eps:

Episode#:49560 reward:-140.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49561 reward:-146.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49562 reward:-117.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49563 reward:-117.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49564 reward:-141.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49565 reward:-118.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49566 reward:-118.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49567 reward:-118.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49568 reward:-115.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49569 reward:-115.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49570 reward:-117.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49571 reward:-119.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49572 reward:-137.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49573 reward:-153.0 best_reward:-89.0 eps:

Episode#:49681 reward:-179.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49682 reward:-152.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49683 reward:-144.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49684 reward:-117.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49685 reward:-115.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49686 reward:-118.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49687 reward:-149.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49688 reward:-155.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49689 reward:-184.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49690 reward:-180.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49691 reward:-115.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49692 reward:-122.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49693 reward:-200.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49694 reward:-143.0 best_reward:-89.0 eps:

Episode#:49804 reward:-141.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49805 reward:-116.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49806 reward:-186.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49807 reward:-154.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49808 reward:-145.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49809 reward:-123.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49810 reward:-143.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49811 reward:-142.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49812 reward:-200.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49813 reward:-125.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49814 reward:-118.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49815 reward:-185.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49816 reward:-124.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49817 reward:-200.0 best_reward:-89.0 eps:

Episode#:49925 reward:-124.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49926 reward:-200.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49927 reward:-147.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49928 reward:-129.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49929 reward:-188.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49930 reward:-124.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49931 reward:-120.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49932 reward:-200.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49933 reward:-119.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49934 reward:-200.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49935 reward:-156.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49936 reward:-116.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49937 reward:-148.0 best_reward:-89.0 eps:0.0049999999486979654
Episode#:49938 reward:-153.0 best_reward:-89.0 eps: